In [ ]:
from transformers import pipeline

classifier = pipeline("zero-shot-classification",
                      model="facebook/bart-large-mnli")


text2 = "Virat Kohli scored a match-winning century against Australia at the Wankhede Stadium."
labels = ["cricket", "politics", "entertainment"]

result2 = classifier(text2, labels)
print("Classification:\n", result2)


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/1.63G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

Device set to use cuda:0


Classification:
 {'sequence': 'Virat Kohli scored a match-winning century against Australia at the Wankhede Stadium.', 'labels': ['cricket', 'entertainment', 'politics'], 'scores': [0.9329296350479126, 0.061923813074827194, 0.0051465327851474285]}


One-Shot Learning

In [ ]:
import numpy as np
import openai
from openai import OpenAI
from sklearn.metrics.pairwise import cosine_similarity

client = OpenAI(api_key="Yours OpenAi Api Key")

def get_embedding(text):
    response = client.embeddings.create(
        model="text-embedding-3-small",
        input=text
    )
    return np.array(response.data[0].embedding)

def one_shot_classify(query, support_examples):
    query_emb = get_embedding(query)

    best_class = None
    best_score = -1

    for cls, example in support_examples.items():
        example_emb = get_embedding(example)
        score = cosine_similarity([query_emb], [example_emb])[0][0]

        print(f"Similarity with {cls}: {score:.4f}")

        if score > best_score:
            best_class = cls
            best_score = score

    return best_class


support_set = {
    "Sports": "A football match was played yesterday.",
    "Technology": "New AI chips are becoming faster.",
    "Food": "This recipe requires tomatoes and spices."
}

query_text = "Nvidia released a new graphics processor."

predicted = one_shot_classify(query_text, support_set)

print("\nPredicted class:", predicted)


Similarity with Sports: 0.1087
Similarity with Technology: 0.5019
Similarity with Food: 0.0548

Predicted class: Technology


Few-Shot Learning


In [ ]:
import numpy as np
import openai
from openai import OpenAI
from sklearn.metrics.pairwise import cosine_similarity

client = OpenAI(api_key="Your OpenAi Api Key")

def get_embedding(text):
    response = client.embeddings.create(
        model="text-embedding-3-small",
        input=text
    )
    return np.array(response.data[0].embedding)

def few_shot_classify(query, support_examples):
    query_emb = get_embedding(query)
    best_class = None
    best_score = -1

    for cls, examples in support_examples.items():
        example_embs = np.array([get_embedding(ex) for ex in examples])
        class_emb = np.mean(example_embs, axis=0)
        score = cosine_similarity([query_emb], [class_emb])[0][0]
        print(f"Similarity with {cls}: {score:.4f}")
        if score > best_score:
            best_class = cls
            best_score = score

    return best_class

support_set = {
    "Sports": [
        "A football match was played yesterday.",
        "The cricket team won the tournament."
    ],
    "Technology": [
        "New AI chips are becoming faster.",
        "Quantum computing is the future."
    ],
    "Food": [
        "This recipe requires tomatoes and spices.",
        "Pasta is cooked with fresh ingredients."
    ]
}

query_text = "Intel announced a new AI processor."
predicted = few_shot_classify(query_text, support_set)

print("\nPredicted class:", predicted)


Similarity with Sports: 0.0754
Similarity with Technology: 0.5980
Similarity with Food: 0.0819

Predicted class: Technology
